It is a very basic kernel for someone who is gettiing started in the field of data science.
I have tried to predict loan application approvals with a relatively small dataset.
Below are the steps that have been carried out in the Kernel.
1. Pre Processing the Dataset
2. Splitting the Input and the Target
3. Standardizing the Dataset
4. Splitting the Input and Target into Test and Train dataset
5. Creating the Model
6. Testing the Model

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the "../input/" directory.
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# Any results you write to the current directory are saved as output.

/kaggle/input/loan-predication/train_u6lujuX_CVtuZ9i (1).csv


Importing the Relevant libraries to be used in the Kernel

In [2]:
import numpy as np
import pandas as pd
import pandas_profiling
from sklearn.linear_model import LogisticRegressionCV, SGDClassifier, LogisticRegression
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, confusion_matrix

Loading the Dataset

In [3]:
raw_csv_data = pd.read_csv("../input/loan-predication/train_u6lujuX_CVtuZ9i (1).csv")

So the first step is preprocessing.
In preprocessing we will try to identify the following points.
1. Checking the numerical and categorical variables.
2. Checking for the missing values.
3. Filling the missing values with dummy values.
4. Mapping the categorical variables
5. Deleting the unwanted columns.

I will use the Pandas Profiling to see the different variables used in the dataset.
It will help us identify the missing values, outliers in the dataset.

In [4]:
raw_csv_data.profile_report()

Map all the categorical values with numerical

In [5]:
raw_csv_data['Gender'] = raw_csv_data['Gender'].map({'Male':1,'Female':0})
raw_csv_data['Married'] = raw_csv_data['Married'].map({'Yes':1,'No':0})
raw_csv_data['Education'] = raw_csv_data['Education'].map({'Graduate':1,'Not Graduate':0})
raw_csv_data['Self_Employed'] = raw_csv_data['Self_Employed'].map({'Yes':1,'No':0})
raw_csv_data['Property_Area'] = raw_csv_data['Property_Area'].map({'Urban':1,'Rural':2,'Semiurban':3})
raw_csv_data['Loan_Status'] = raw_csv_data['Loan_Status'].map({'Y':1,'N':0})

In [6]:
raw_csv_data

Loan_ID  Gender  Married Dependents  Education  Self_Employed  \
0    LP001002     1.0      0.0          0          1            0.0   
1    LP001003     1.0      1.0          1          1            0.0   
2    LP001005     1.0      1.0          0          1            1.0   
3    LP001006     1.0      1.0          0          0            0.0   
4    LP001008     1.0      0.0          0          1            0.0   
..        ...     ...      ...        ...        ...            ...   
609  LP002978     0.0      0.0          0          1            0.0   
610  LP002979     1.0      1.0         3+          1            0.0   
611  LP002983     1.0      1.0          1          1            0.0   
612  LP002984     1.0      1.0          2          1            0.0   
613  LP002990     0.0      0.0          0          1            1.0   

     ApplicantIncome  CoapplicantIncome  LoanAmount  Loan_Amount_Term  \
0               5849                0.0         NaN             360.0   
1               4583             1508.0       128.0             360.0   
2               3000                0.0        66.0             360.0   
3               2583             2358.0       120.0             360.0   
4               6000                0.0       141.0             360.0   
..               ...                ...         ...               ...   
609             2900                0.0        71.0             360.0   
610             4106                0.0        40.0             180.0   
611             8072              240.0       253.0             360.0   
612             7583                0.0       187.0             360.0   
613             4583                0.0       133.0             360.0   

     Credit_History  Property_Area  Loan_Status  
0               1.0              1            1  
1               1.0              2            0  
2               1.0              1            1  
3               1.0              1            1  
4               1.0              1            1  
..              ...            ...          ...  
609             1.0              2            1  
610             1.0              2            1  
611             1.0              1            1  
612             1.0              1            1  
613             0.0              3            0  

[614 rows x 13 columns]

As we can see that the column Dependents have some values as 3+.
We will create 4 cloumns as Dependent_1, Dependent_2, Dependent_3, Dependent_4 for each(0,1,2,3+) and map all the values with 1.

In [7]:
#Keeping a checkpoint
pre_process_data = raw_csv_data

In [8]:
##Insert new columns for dependents
pre_process_data.insert(0, "Dependents_1", 0) 
pre_process_data.insert(1, "Dependents_2", 0) 
pre_process_data.insert(2, "Dependents_3", 0) 
pre_process_data.insert(3, "Dependents_4", 0) 

In [9]:
#Fill all the values for newly created Dependent Column.
for ind in pre_process_data.index: 
     if(pre_process_data['Dependents'][ind] == 0):
        pre_process_data['Dependents_1'][ind] = 1
     elif(pre_process_data['Dependents'][ind] == 1):
        pre_process_data['Dependents_2'][ind] = 1
     elif(pre_process_data['Dependents'][ind] == 2):
        pre_process_data['Dependents_3'][ind] = 1
     elif(pre_process_data['Dependents'][ind] == '3+'):
        pre_process_data['Dependents_4'][ind] = 1

In [10]:
##Drop the Loan Id and the Dependent Column.
pre_process_data = pre_process_data.drop(['Dependents'], axis=1)
pre_process_data = pre_process_data.drop(['Loan_ID'], axis=1)

As we see that there are lot of missing values in the dataset, we will use the Simple Impute from the scikit library to fill the missing values with the dummy values.

In [11]:
##Get Dummies
dummies= pd.get_dummies(pre_process_data, drop_first=True)

# We will now impute values
SimImp = SimpleImputer()
pre_process_data = pd.DataFrame(SimImp.fit_transform(dummies), columns=dummies.columns)

In [12]:
##All the missing values have been filled.
pre_process_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 614 entries, 0 to 613
Data columns (total 15 columns):
Dependents_1         614 non-null float64
Dependents_2         614 non-null float64
Dependents_3         614 non-null float64
Dependents_4         614 non-null float64
Gender               614 non-null float64
Married              614 non-null float64
Education            614 non-null float64
Self_Employed        614 non-null float64
ApplicantIncome      614 non-null float64
CoapplicantIncome    614 non-null float64
LoanAmount           614 non-null float64
Loan_Amount_Term     614 non-null float64
Credit_History       614 non-null float64
Property_Area        614 non-null float64
Loan_Status          614 non-null float64
dtypes: float64(15)
memory usage: 72.1 KB


As the Column Loan Status is our Target, we will split the target.
After that we will Standardize the Input by using Standard Scaler of Sklearn.

In [13]:
unscaled_inputs=pre_process_data.iloc[:,:-1]

##Standardize the input
from sklearn.preprocessing import StandardScaler
loan_scaler = StandardScaler()
loan_scaler.fit(unscaled_inputs)

StandardScaler(copy=True, with_mean=True, with_std=True)

In [14]:
scaled_inputs = loan_scaler.transform(unscaled_inputs)
scaled_inputs

array([[ 0.        ,  0.        ,  0.        , ...,  0.27985054,
         0.45164045, -1.25029822],
       [ 0.        ,  0.        ,  0.        , ...,  0.27985054,
         0.45164045, -0.06009185],
       [ 0.        ,  0.        ,  0.        , ...,  0.27985054,
         0.45164045, -1.25029822],
       ...,
       [ 0.        ,  0.        ,  0.        , ...,  0.27985054,
         0.45164045, -1.25029822],
       [ 0.        ,  0.        ,  0.        , ...,  0.27985054,
         0.45164045, -1.25029822],
       [ 0.        ,  0.        ,  0.        , ...,  0.27985054,
        -2.41044061,  1.13011452]])

In [15]:
##Splitting the Target
targets = pre_process_data['Loan_Status'] 

Now we will split the data into Test and Train using test_train_split from Sklearn

In [16]:
##Split the data into train test and shuffle
from sklearn.model_selection import train_test_split
train_test_split(scaled_inputs,targets)

[array([[ 0.        ,  0.        ,  0.        , ...,  0.27985054,
         -2.41044061, -0.06009185],
        [ 0.        ,  0.        ,  0.        , ...,  0.27985054,
          0.45164045,  1.13011452],
        [ 0.        ,  0.        ,  0.        , ...,  0.27985054,
          0.45164045,  1.13011452],
        ...,
        [ 0.        ,  0.        ,  0.        , ...,  0.27985054,
          0.45164045, -0.06009185],
        [ 0.        ,  0.        ,  0.        , ...,  0.27985054,
          0.45164045,  1.13011452],
        [ 0.        ,  0.        ,  0.        , ...,  0.27985054,
          0.45164045,  1.13011452]]),
 array([[ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
          2.79850543e-01,  4.51640451e-01,  1.13011452e+00],
        [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
          2.79850543e-01,  4.51640451e-01, -6.00918525e-02],
        [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
          2.79850543e-01,  4.51640451e-01,  1.13011452e+

Create the Model

In [17]:
 ##Logistic Regression with SKlearn
from sklearn.linear_model import LogisticRegression
from sklearn import metrics

x_train, x_test, y_train, y_test = train_test_split(scaled_inputs,targets, train_size=0.8)

##Training the Model
reg=LogisticRegression()
reg.fit(x_train,y_train)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='warn', n_jobs=None, penalty='l2',
                   random_state=None, solver='warn', tol=0.0001, verbose=0,
                   warm_start=False)

Check the Accuracy of the Model

In [18]:
reg.score(x_train,y_train)

0.8024439918533605

As you see that there is 80% accuracy of the Model.
Now we will test our model with the test data that we had splitted before.

In [19]:
##Testing the Model
reg.score(x_test,y_test)

0.8455284552845529

Our Model gives around 82% accuracy with the test data.
Thanks for seeing the kernel.
Please provide your Comments and suggestion as I am still in the initial learning phase.